In [12]:
import numpy as np
import mne
import os 
from scipy.io import loadmat
import random

In [13]:
num_channels = 32 

In [14]:
# Creating mne.info object
channel_names = ['Fp1','AF3','F3','F7','FC5','FC1','C3','T7','CP5','CP1','P3','P7','PO3','O1','Oz','Pz','Fp2','AF4','Fz','F4','F8','FC6','FC2','Cz','C4','T8','CP6','CP2','P4','P8','PO4','O2']
num_channels = len(channel_names)
channel_types= ['eeg' for x in range(num_channels)]
sfreq = 128 
info = mne.create_info(channel_names, sfreq, channel_types)

In [15]:
# Define EEG bands
eeg_bands = {'Delta': (1,3),
             'Theta': (4, 7),
             'Alpha': (8, 13),
             'Beta': (14, 30),
             'Gamma': (31, 50)}
list_keys = list(eeg_bands.keys())

In [16]:
tmin = 0.0  # start of each epoch (0ms before the trigger)
tmax = 1  # end of each epoch (1s after the trigger)
baseline = (0, 0)  # means from the first instant to t = 0

In [17]:
def create_model_input_files():
    os.chdir("/home/shreya/DEAP/Data_32subjects/")
    for file in os.listdir():
        print(file)
        content = loadmat(file)
        data = content['data']
        labels = content['labels']
#         data = datapart of the content
        
        ## Picking the 32 electrodes and 3 second pre-trial baseline
        eeg_electrodes_data = data[:,0:32,384:]
        print(eeg_electrodes_data.shape)
        
        file_suffix = file[:-4]
        #Generate 4 random numbers between 0 and 31  -- splitting trials in train and test
        test_list = random.sample(range(0, 40), 4)

        print("test list - ", test_list)
        ## Separating the trials for each subject 
        separating_trials(test_list, labels, eeg_electrodes_data, file_suffix)
#         break

In [18]:
def define_events(raw, max_length, dist_bw_events):
    sample_no_event = np.arange(0, max_length, dist_bw_events).transpose()
    sample_no_event = sample_no_event.reshape(sample_no_event.shape[0],1)
    duration_event = np.zeros_like(sample_no_event)
    int_event_code = duration_event + 1
    events = np.concatenate((sample_no_event , duration_event, int_event_code), axis = 1)
    return events

In [19]:
def save_features(folder1, folder2, feaures, file_suffix, task_valence, task_arousal):
    for w in range(feaures.shape[0]):            
#         # Task 1
#         if task_valence == True:
#             n_folder1 = folder1 + "HighValence/"
#         elif task_valence == False:
#             n_folder1 = folder1 +"LowValence/"
#         else:
#             n_folder1 = folder1 + "NoneValence/"
            
#         filename1 = n_folder1 + file_suffix + "_" + str(w)
#         np.save(filename1,feaures[w])
#         print("saved file - ", filename1)
        
        # Task 2
        if task_arousal == True:
            n_folder2 = folder2 + "HighArousal/"
        elif task_arousal == False:
            n_folder2 = folder2 + "LowArousal/"
        else:
            n_folder2 = folder2 + "NoneArousal/"
            
        filename2 = n_folder2 + file_suffix + "_" + str(w)
        np.save(filename2,feaures[w])
        print("saved file - ", filename2)
#         break

In [20]:
def psd_features(epochs):
    psds, freqs = mne.time_frequency.psd_welch(epochs,  n_fft = 128, average='mean')
    
#     print(freqs)
    band_psd = dict()
    ## band wise psd features 
    for band in eeg_bands:  
        ## finding indices for each band
        freq_ix = np.where((freqs >= eeg_bands[band][0]) & (freqs <= eeg_bands[band][1]))[0]
        
        # calculating mean of the log of psd values of the band
        psd_vals = np.log(np.sum(psds[:,:,freq_ix], axis=2))
        psd_vals = psd_vals.reshape((psd_vals.shape[0], psd_vals.shape[1], 1))
        band_psd[band] = psd_vals
    
    #Creating Feature Array
    feature_arr = band_psd[list_keys[0]]
    for i in range(1,len(list_keys)):
        feature_arr = np.concatenate((feature_arr, band_psd[list_keys[i]]), axis=2)
        
    feature_arr = feature_arr.reshape((feature_arr.shape[0], 1, feature_arr.shape[1], feature_arr.shape[2]))
    print(feature_arr.shape)
    
    return feature_arr

In [21]:
def separating_trials(test_list, labels, data, file_suffix):
    for trial_no in range(data.shape[0]):
        print(trial_no)

        ## Creating mne.Raw object 
        raw = mne.io.RawArray(data[trial_no], info)
        raw.load_data()
        
        ## Creating epochs
        events = define_events(raw, 7680, 128)
        epochs = mne.Epochs(raw, events, event_id=1, tmin=tmin, tmax=tmax, proj=True, baseline=baseline)

        # Calculating band psd features 
        feature_arr = psd_features(epochs)
        
        new_file_suffix = file_suffix + "_" + str(trial_no)
        if trial_no in test_list:
            folder1 = "/home/shreya/DEAP/TaskValence/Test/"
            folder2 = "/home/shreya/DEAP/TaskArousal/Test/"
        else:
            folder1 = "/home/shreya/DEAP/TaskValence/Train/"
            folder2 = "/home/shreya/DEAP/TaskArousal/Train/"
        
        #trial x label (valence, arousal, dominance, liking)
        task_valence =  None
        task_arousal = None
        if 1 <= labels[trial_no][0] and labels[trial_no][0] <= 4.8:
            task_valence =  False 
        elif 5.2 <= labels[trial_no][0] and labels[trial_no][0] <= 9:
            task_valence =  True
        else:
            print("not in any range, task_valence")
        
        if 1 <= labels[trial_no][1] and labels[trial_no][1] <= 4.8:
            task_arousal =  False 
        elif 5.2 <= labels[trial_no][1] and labels[trial_no][1] <= 9:
            task_arousal =  True
        else:
            print("not in any range, task_arousal")
        # saving as .npy files 
        save_features(folder1, folder2, feature_arr, new_file_suffix, task_valence, task_arousal)
        
#         break

In [22]:
create_model_input_files()

s06.mat
(40, 32, 7680)
test list -  [22, 19, 27, 0]
0
Creating RawArray with float64 data, n_channels=32, n_times=7680
    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
60 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 60 events and 129 original time points ...
1 bad epochs dropped
Effective window size : 1.000 (s)
(59, 1, 32, 5)
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_0
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_1
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_2
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_3
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_4
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_5
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_6
saved file -  /home/shreya/DEAP/TaskArousal/Test/LowArousal/s06_0_7
saved file -  /home/shreya/D

    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
60 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 60 events and 129 original time points ...
1 bad epochs dropped
Effective window size : 1.000 (s)
(59, 1, 32, 5)
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_0
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_1
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_2
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_3
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_4
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_5
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_6
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_7
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_2_8
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal

    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
60 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 60 events and 129 original time points ...
1 bad epochs dropped
Effective window size : 1.000 (s)
(59, 1, 32, 5)
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_0
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_1
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_2
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_3
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_4
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_5
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_6
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_7
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_4_8
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal

    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
60 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 60 events and 129 original time points ...
1 bad epochs dropped
Effective window size : 1.000 (s)
(59, 1, 32, 5)
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_0
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_1
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_2
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_3
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_4
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_5
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_6
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_7
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s06_6_8
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal

saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_48
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_49
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_50
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_51
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_52
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_53
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_54
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_55
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_56
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_57
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s06_7_58
8
Creating RawArray with float64 data, n_channels=32, n_times=7680
    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
60 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection 

...

saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_34
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_35
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_36
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_37
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_38
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_39
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_40
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_41
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_42
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_43
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_44
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_45
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_31_46
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s1

saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_27
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_28
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_29
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_30
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_31
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_32
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_33
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_34
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_35
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_36
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_37
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_38
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s11_33_39
saved file -  /home/shreya/DEAP/TaskArousal/Train/NoneArousal/s1

saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_29
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_30
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_31
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_32
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_33
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_34
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_35
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_36
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_37
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_38
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_39
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_40
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_35_41
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s1

saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_27
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_28
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_29
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_30
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_31
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_32
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_33
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_34
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_35
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_36
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_37
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_38
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s11_37_39
saved file -  /home/shreya/DEAP/TaskArousal/Train/HighArousal/s1

saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_26
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_27
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_28
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_29
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_30
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_31
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_32
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_33
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_34
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_35
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_36
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_37
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_38
saved file -  /home/shreya/DEAP/TaskArousal/Train/LowArousal/s11_39_39
saved 